In [2]:
import pandas as pd
import CococoNet_reader 
import itertools
import numpy as np
import Name_resolver

In [1]:
def Calculate_Score_list_for_thresholding(Species_1 = 'rice',Species_2 = 'maize'):

    import pandas as pd
    import CococoNet_reader
    #Get Species Names in Common form 
    common_name_1 = Name_resolver.species_name_resolver(Species_1,'common')
    common_name_2 = Name_resolver.species_name_resolver(Species_2,'common')


    matrix_of_locations = pd.read_csv('/data/passala/git/Coexpressalog_Method_Development/Cross_all_species/map_of_ortholog_map_locations.csv', index_col= 0)#List of cross species maps
    current_location = matrix_of_locations[common_name_1][common_name_2] #get string for map
    
    cross_species_n_m_genes = pd.read_csv(current_location)

    ### Get one to ones
    cross_species_map_one_to_one = cross_species_n_m_genes.drop_duplicates(subset=common_name_1, keep= False,)
    cross_species_map_one_to_one = cross_species_map_one_to_one.drop_duplicates(subset= common_name_2, keep= False)

    ## Convert to Dictionary
    dictionary_mapper_one_to_two = cross_species_map_one_to_one.set_index(common_name_1).to_dict()[common_name_2]
    dictionary_mapper_dos_to_uno = cross_species_map_one_to_one.set_index(common_name_2).to_dict()[common_name_1]

    ## Read In Cococonets 
    coconet_species_one = CococoNet_reader.read_cococonet(common_name_1)
    coconet_species_two = CococoNet_reader.read_cococonet(common_name_2)

    cross_species_n_m_genes['Group ID'] = 'Unassigned'
    

    ## Assign Genes to Groups
    id_indexer = 0
    for gene_pair in cross_species_n_m_genes.iterrows():
        
        if gene_pair[1]['Group ID'] == 'Unassigned':
            current_species_1_gene = gene_pair[1][common_name_1]
            current_species_2_gene = gene_pair[1][common_name_2]
            cross_species_n_m_genes['Group ID'].loc[(cross_species_n_m_genes[common_name_1] == current_species_1_gene) & (cross_species_n_m_genes['Group ID'] == 'Unassigned')] = id_indexer
            cross_species_n_m_genes['Group ID'].loc[(cross_species_n_m_genes[common_name_2] == current_species_2_gene) & (cross_species_n_m_genes['Group ID'] == 'Unassigned')] = id_indexer

            all_labeled_groups = cross_species_n_m_genes.loc[cross_species_n_m_genes['Group ID'] == id_indexer]

            all_labeled_groups_species_1_genes = all_labeled_groups[common_name_1].to_list()
            all_labeled_groups_species_2_genes = all_labeled_groups[common_name_2].to_list()

            cross_species_n_m_genes['Group ID'].loc[cross_species_n_m_genes[common_name_1].isin(all_labeled_groups_species_1_genes)] = id_indexer
            cross_species_n_m_genes['Group ID'].loc[cross_species_n_m_genes[common_name_2].isin(all_labeled_groups_species_2_genes)] = id_indexer

            id_indexer += 1



    #Identify Pairs for evaluation
    all_pairs_to_evaluate_for_functional_conservation = pd.DataFrame(columns = [common_name_1,common_name_2,'Group Number'])
    for group_number in list(set(cross_species_n_m_genes['Group ID'].to_list())):
        current_gene_map = cross_species_n_m_genes.loc[cross_species_n_m_genes['Group ID'] == group_number]
        list_of_species_1_genes_in_group = list(set(current_gene_map[common_name_1].to_list()))
        list_of_species_2_genes_in_group = list(set(current_gene_map[common_name_2].to_list()))
        all_combo_list_current_genes = itertools.product(list_of_species_1_genes_in_group,list_of_species_2_genes_in_group)
        all_combo_list_current_genes = list(map(list,all_combo_list_current_genes))
        current_list_of_pairs = pd.DataFrame(all_combo_list_current_genes,columns = [Species_1,Species_2])
        current_list_of_pairs['Group Number'] = group_number
        all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)


    
    all_pairs_to_evaluate_for_functional_conservation['Species 1 Score'] = np.nan
    all_pairs_to_evaluate_for_functional_conservation['Species 2 Score'] = np.nan


    ## Trim cococonets to match


    trimmed_species_1_cococonet = coconet_species_one[coconet_species_one.columns.intersection(cross_species_n_m_genes[common_name_1].to_list())]
    trimmed_species_1_cococonet = trimmed_species_1_cococonet[trimmed_species_1_cococonet.index.isin(cross_species_n_m_genes[common_name_1].to_list())]
    double_species_1_trimmed_cococonet = trimmed_species_1_cococonet[trimmed_species_1_cococonet.columns.intersection(cross_species_map_one_to_one[common_name_1].to_list())]
    double_species_1_trimmed_cococonet = double_species_1_trimmed_cococonet.replace(1,0)

    trimmed_species_2_cococonet = coconet_species_two[coconet_species_two.columns.intersection(cross_species_n_m_genes[common_name_2].to_list())]
    trimmed_species_2_cococonet = trimmed_species_2_cococonet[trimmed_species_2_cococonet.index.isin(cross_species_n_m_genes[common_name_2].to_list())]
    double_species_2_trimmed_cococonet = trimmed_species_2_cococonet[trimmed_species_2_cococonet.columns.intersection(cross_species_map_one_to_one[common_name_2].to_list())]
    double_species_2_trimmed_cococonet = double_species_2_trimmed_cococonet.replace(1,0)


    ## Rank
    species_1_cococonet_ranked = trimmed_species_1_cococonet.rank()
    species_2_cococonet_ranked = trimmed_species_2_cococonet.rank()

    #Do top 10 Genes
    top_10_species_1_genes = np.array(
        [double_species_1_trimmed_cococonet.T[c].nlargest(10).index.values for c in double_species_1_trimmed_cococonet.T]
    )  # using pair list above, cut down top 10 list to relevant genes, probably by adding list as a column in panda and then filtering panda to index of pair list
    top_10_species_1_genes_dataframe = pd.DataFrame(
        data=top_10_species_1_genes,
        index=double_species_1_trimmed_cococonet.index,
        columns=[
            "One",
            "Two",
            "Three",
            "Four",
            "Five",
            "Six",
            "Seven",
            "Eight",
            "Nine",
            "Ten",
        ],
    )

    #Convert 
    top_10_species_1_genes_as_species_2 = top_10_species_1_genes_dataframe.replace(to_replace=dictionary_mapper_one_to_two)

    # Get genes for checking 
    have_species_1_pairs = all_pairs_to_evaluate_for_functional_conservation.loc[all_pairs_to_evaluate_for_functional_conservation[common_name_1].isin(top_10_species_1_genes_as_species_2.index)]
    trimmed_all_gene_pairs_for_fc = have_species_1_pairs.loc[have_species_1_pairs[common_name_2].isin(trimmed_species_2_cococonet.index)]
    trimmed_all_gene_pairs_for_fc = trimmed_all_gene_pairs_for_fc.reset_index(drop = True)

    # Get values in species 2 
    for two_genes in trimmed_all_gene_pairs_for_fc.iterrows():
        current_species_1_gene = two_genes[1][common_name_1]
        current_species_2_gene = two_genes[1][common_name_2]
        finger_print_genes = top_10_species_1_genes_as_species_2.loc[current_species_1_gene].to_list()
        gene_ranks_in_species_2 = species_2_cococonet_ranked.loc[species_2_cococonet_ranked.index.isin(finger_print_genes), current_species_2_gene]
        avg_rank_in_species_2 = gene_ranks_in_species_2.mean()
        index_from_pairs = two_genes[0]
        trimmed_all_gene_pairs_for_fc.at[index_from_pairs, 'Species 1 Score'] = avg_rank_in_species_2

    #Repeat for Species 2 

    top_10_species_2_genes = np.array(
        [double_species_2_trimmed_cococonet.T[c].nlargest(10).index.values for c in double_species_2_trimmed_cococonet.T]
    )  # using pair list above, cut down top 10 list to relevant genes, probably by adding list as a column in panda and then filtering panda to index of pair list
    top_10_species_2_genes_dataframe = pd.DataFrame(
        data=top_10_species_2_genes,
        index=double_species_2_trimmed_cococonet.index,
        columns=[
            "One",
            "Two",
            "Three",
            "Four",
            "Five",
            "Six",
            "Seven",
            "Eight",
            "Nine",
            "Ten",
        ],
    )
    

    #convert 
    top_10_species_2_genes_as_species_1 = top_10_species_2_genes_dataframe.replace(to_replace=dictionary_mapper_dos_to_uno)


    # Get values in species 1 
    for two_genes in trimmed_all_gene_pairs_for_fc.iterrows():
        current_species_1_gene = two_genes[1][common_name_1]
        current_species_2_gene = two_genes[1][common_name_2]
        finger_print_genes = top_10_species_2_genes_as_species_1.loc[current_species_2_gene].to_list()
        gene_ranks_in_species_1 = species_1_cococonet_ranked.loc[species_1_cococonet_ranked.index.isin(finger_print_genes), current_species_1_gene]
        avg_rank_in_species_1 = gene_ranks_in_species_1.mean()
        index_from_pairs = two_genes[0]
        trimmed_all_gene_pairs_for_fc.loc[index_from_pairs, 'Species 2 Score'] = avg_rank_in_species_1
    
    #Caluclate Divisors 
    Number_of_species_1_genes = len(top_10_species_1_genes_as_species_2)
    Number_of_species_2_genes = len(top_10_species_2_genes_as_species_1)


    species_1_score_divisor = Number_of_species_2_genes - 4.5
    species_2_score_divisor = Number_of_species_1_genes-4.5

    #Divide and Average 
    trimmed_all_gene_pairs_for_fc['Species 1 Score'] = trimmed_all_gene_pairs_for_fc['Species 1 Score']/species_1_score_divisor
    trimmed_all_gene_pairs_for_fc['Species 2 Score'] = trimmed_all_gene_pairs_for_fc['Species 2 Score']/species_2_score_divisor
    trimmed_all_gene_pairs_for_fc['Total Score'] = trimmed_all_gene_pairs_for_fc[['Species 1 Score','Species 2 Score']].mean(axis = 1)
    
    return trimmed_all_gene_pairs_for_fc
    

In [4]:
Calculate_Score_list_for_thresholding(Species_1 = 'grape',Species_2 = 'tobacco')


KeyError: Index(['tobacco'], dtype='object')

In [33]:
def Threshold_and_generate_coexpressalog_list(trimmed_all_gene_pairs_for_fc, single_pair_junk_threshold = .8, many_to_many_junk_threshold = .85,difference_between_many_to_drop = .03):
    
    
    list_of_true_pairs = []
    list_of_genes_to_average_and_set_to_be_equal = []


    common_name_1 = trimmed_all_gene_pairs_for_fc.columns[0]
    common_name_2 = trimmed_all_gene_pairs_for_fc.columns[1]

    for current_group in list(set(trimmed_all_gene_pairs_for_fc['Group Number'].to_list())):
        dataframe_of_group = trimmed_all_gene_pairs_for_fc.loc[trimmed_all_gene_pairs_for_fc['Group Number'] == current_group]
        dataframe_of_group = dataframe_of_group[[common_name_1,common_name_2,'Total Score']]
        wide_format = dataframe_of_group.pivot(index = common_name_1,columns= common_name_2,values= 'Total Score')
        if (wide_format<single_pair_junk_threshold).all(axis = None):
            continue
        elif wide_format.shape ==(0,0):
            continue
        elif wide_format.shape == (1,1): # Group is 1 to 1, retain Format: Arabidopsis then Maize
            one_true_pair = [wide_format.index.item(),wide_format.columns.item()]
            list_of_true_pairs.append(one_true_pair)
        elif len(wide_format)>1 and len(wide_format.columns) ==1:
            one_true_pair = [wide_format.idxmax(axis =0).item(),wide_format.columns.item()]
            list_of_true_pairs.append(one_true_pair)
        elif len(wide_format) == 1 and len(wide_format.columns)>1:
            one_true_pair = [wide_format.index.item(), wide_format.idxmax(axis = 1).item()]
            list_of_true_pairs.append(one_true_pair)
        else:

            #Drop Low Quality Columns and Rows
            cols_to_drop = wide_format.columns[wide_format.max()<many_to_many_junk_threshold]
            wide_format = wide_format.drop(columns= cols_to_drop)
            rows_to_drop = wide_format.index[wide_format.max(axis = 1)<many_to_many_junk_threshold]
            wide_format = wide_format.drop(index= rows_to_drop)
            if (wide_format<single_pair_junk_threshold).all(axis = None):
                continue
            elif wide_format.shape ==(0,0):
                continue
            elif wide_format.shape == (1,1): # Group is 1 to 1, retain Format: Arabidopsis then Maize
                one_true_pair = [wide_format.index.item(),wide_format.columns.item()]
                list_of_true_pairs.append(one_true_pair)
            elif len(wide_format)>1 and len(wide_format.columns) ==1:
                one_true_pair = [wide_format.idxmax(axis =0).item(),wide_format.columns.item()]
                list_of_true_pairs.append(one_true_pair)
            elif len(wide_format) == 1 and len(wide_format.columns)>1:
                one_true_pair = [wide_format.index.item(), wide_format.idxmax(axis = 1).item()]
                list_of_true_pairs.append(one_true_pair)
            elif (wide_format>.9).all(axis = None):
                ### Put in retention code here
                both_gene_lists_to_average = [wide_format.index.to_list(), wide_format.columns.to_list()]
                list_of_genes_to_average_and_set_to_be_equal.append(both_gene_lists_to_average)
                
            else:
                for cur_row in wide_format.iterrows():
                    cur_row_max = cur_row[1].max()
                    cur_row[1][cur_row[1]< cur_row_max - difference_between_many_to_drop] = np.nan
                    wide_format.loc[cur_row[0]] = cur_row[1]
                wide_format = wide_format.dropna(axis = 1, how = 'all')
                for cur_col in wide_format.columns:
                    cur_col_max = wide_format[cur_col].max()
                    wide_format[cur_col].loc[wide_format[cur_col]< cur_col_max-difference_between_many_to_drop] = np.nan
                wide_format = wide_format.dropna(axis = 0, how = 'all')
                col_count = wide_format.count() == 1
                wide_format = wide_format.loc[:,col_count]
                row_count = wide_format.count(axis = 1) ==1 
                wide_format = wide_format.loc[row_count,:]
                wide_format = wide_format.dropna(axis = 1, how = 'all')
                wide_format = wide_format.dropna(axis = 0, how = 'all')
                for label,content in wide_format.items():
                    cur_species_2_label = label
                    cur_species_1_label = content.idxmax()
                    if type(cur_species_1_label) == str:
                        one_true_pair = [cur_species_1_label,cur_species_2_label]
                        list_of_true_pairs.append(one_true_pair)


    true_pair_dataframe = pd.DataFrame(columns= [f'{common_name_1} gene',f'{common_name_2} gene'], data = list_of_true_pairs)
    true_pair_dataframe = true_pair_dataframe.drop_duplicates(subset = f'{common_name_1} gene')
    true_pair_dataframe = true_pair_dataframe.drop_duplicates(subset = f'{common_name_2} gene')
    
    return true_pair_dataframe
                

In [35]:
trimmed_all_gene_pairs_for_fc

apple     sorghum Group Number  Species 1 Score  \
0      LOC103444819  LOC8081914            0         0.783045   
1      LOC103444819  LOC8155288            0         0.819706   
2      LOC103401548  LOC8054161            1         0.836989   
3      LOC103417271  LOC8080569            2         0.857503   
4      LOC103426806  LOC8083888            3         0.857372   
...             ...         ...          ...              ...   
19494  LOC103450923  LOC8077323         7107         0.404571   
19495  LOC103455790  LOC8077323         7107         0.557902   
19496  LOC103440894  LOC8077323         7107         0.583460   
19497  LOC103432817  LOC8072511         7109         0.768830   
19498  LOC103437184  LOC8072511         7109         0.740554   

       Species 2 Score  Total Score  
0             0.750795     0.766920  
1             0.920683     0.870195  
2             0.838693     0.837841  
3             0.720475     0.788989  
4             0.917930     0.887651  
...                ...          ...  
19494         0.503088     0.453829  
19495         0.694277     0.626089  
19496         0.693067     0.638264  
19497         0.736281     0.752556  
19498         0.871170     0.805862  

[19499 rows x 6 columns]

In [34]:
Threshold_and_generate_coexpressalog_list(trimmed_all_gene_pairs_for_fc)

apple Gene sorghum Gene
0     LOC103444819   LOC8155288
1     LOC103401548   LOC8054161
2     LOC103426806   LOC8083888
3     LOC103447911   LOC8061304
4     LOC103418459   LOC8075043
...            ...          ...
3640  LOC103445290   LOC8072874
3641  LOC103401699   LOC8068771
3642  LOC103424763   LOC8067710
3643  LOC103446550   LOC8058391
3644  LOC103437184   LOC8072511

[3645 rows x 2 columns]

In [28]:
trimmed_all_gene_pairs_for_fc = Calculate_Score_list_for_thresholding('apple','sorghum')

/tmp/ipykernel_2026627/320054889.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/320054889.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/320054889.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/320054889.py:62: FutureWarning: The frame.append method 

In [29]:
trimmed_all_gene_pairs_for_fc

apple     sorghum Group Number  Species 1 Score  \
0      LOC103444819  LOC8081914            0         0.783045   
1      LOC103444819  LOC8155288            0         0.819706   
2      LOC103401548  LOC8054161            1         0.836989   
3      LOC103417271  LOC8080569            2         0.857503   
4      LOC103426806  LOC8083888            3         0.857372   
...             ...         ...          ...              ...   
19494  LOC103450923  LOC8077323         7107         0.404571   
19495  LOC103455790  LOC8077323         7107         0.557902   
19496  LOC103440894  LOC8077323         7107         0.583460   
19497  LOC103432817  LOC8072511         7109         0.768830   
19498  LOC103437184  LOC8072511         7109         0.740554   

       Species 2 Score  Total Score  
0             0.750795     0.766920  
1             0.920683     0.870195  
2             0.838693     0.837841  
3             0.720475     0.788989  
4             0.917930     0.887651  
...                ...          ...  
19494         0.503088     0.453829  
19495         0.694277     0.626089  
19496         0.693067     0.638264  
19497         0.736281     0.752556  
19498         0.871170     0.805862  

[19499 rows x 6 columns]

In [25]:
## Species 1 - rice
## Species 2 - maize

In [6]:
matrix_of_locations = pd.read_csv('/data/passala/git/Coexpressalog_Method_Development/Cross_all_species/map_of_ortholog_map_locations.csv', index_col= 0)


In [7]:
common_name_1 = Name_resolver.species_name_resolver("grape",'common')
common_name_2 = Name_resolver.species_name_resolver("tobacco",'common')
current_location = matrix_of_locations[common_name_1][common_name_2] #get string for map
cross_species_n_m_genes = pd.read_csv(current_location)
cross_species_map_one_to_one = cross_species_n_m_genes.drop_duplicates(subset=common_name_1, keep= False,)
cross_species_map_one_to_one = cross_species_map_one_to_one.drop_duplicates(subset= common_name_2, keep= False)
    

KeyError: Index(['tobacco'], dtype='object')

In [8]:
cross_species_map_one_to_one

tomato         grape tomato_OrthoID   grape_OrthoID
2              TAL  LOC100247241  4081_0:00628e  29760_0:00000d
25    LOC101262162  LOC100249273  4081_0:000d23  29760_0:00002d
53    LOC101255785  LOC100258132  4081_0:0020ca  29760_0:000042
54    LOC104647317  LOC104880641  4081_0:0029b3  29760_0:00004f
57    LOC104646413  LOC100250084  4081_0:0017fe  29760_0:00005d
...            ...           ...            ...             ...
5210  LOC101245209  LOC100854121  4081_0:005358  29760_0:006392
5211  LOC101265698  LOC100241671  4081_0:00578a  29760_0:006394
5212  LOC101261509  LOC100244914  4081_0:002808  29760_0:006397
5213  LOC101268056  LOC100854489  4081_0:0010e9  29760_0:00639f
5214  LOC101251805  LOC100854810  4081_0:00451c  29760_0:0063b1

[1516 rows x 4 columns]

In [4]:
dictionary_mapper_one_to_two = cross_species_map_one_to_one.set_index(common_name_1).to_dict()[common_name_2]
dictionary_mapper_dos_to_uno = cross_species_map_one_to_one.set_index(common_name_2).to_dict()[common_name_1]

In [5]:
coconet_species_one = CococoNet_reader.read_cococonet(common_name_1)
coconet_species_two = CococoNet_reader.read_cococonet(common_name_2)

In [6]:

cross_species_n_m_genes['Group ID'] = 'Unassigned'

id_indexer = 0
for gene_pair in cross_species_n_m_genes.iterrows():
    
    if gene_pair[1]['Group ID'] == 'Unassigned':
        current_species_1_gene = gene_pair[1][common_name_1]
        current_species_2_gene = gene_pair[1][common_name_2]
        cross_species_n_m_genes['Group ID'].loc[(cross_species_n_m_genes[common_name_1] == current_species_1_gene) & (cross_species_n_m_genes['Group ID'] == 'Unassigned')] = id_indexer
        cross_species_n_m_genes['Group ID'].loc[(cross_species_n_m_genes[common_name_2] == current_species_2_gene) & (cross_species_n_m_genes['Group ID'] == 'Unassigned')] = id_indexer

        all_labeled_groups = cross_species_n_m_genes.loc[cross_species_n_m_genes['Group ID'] == id_indexer]

        all_labeled_groups_species_1_genes = all_labeled_groups[common_name_1].to_list()
        all_labeled_groups_species_2_genes = all_labeled_groups[common_name_2].to_list()

        cross_species_n_m_genes['Group ID'].loc[cross_species_n_m_genes[common_name_1].isin(all_labeled_groups_species_1_genes)] = id_indexer
        cross_species_n_m_genes['Group ID'].loc[cross_species_n_m_genes[common_name_2].isin(all_labeled_groups_species_2_genes)] = id_indexer

        id_indexer += 1




In [7]:
all_pairs_to_evaluate_for_functional_conservation = pd.DataFrame(columns = [common_name_1,common_name_2,'Group Number'])
for group_number in list(set(cross_species_n_m_genes['Group ID'].to_list())):
    current_gene_map = cross_species_n_m_genes.loc[cross_species_n_m_genes['Group ID'] == group_number]
    list_of_species_1_genes_in_group = list(set(current_gene_map[common_name_1].to_list()))
    list_of_species_2_genes_in_group = list(set(current_gene_map[common_name_2].to_list()))
    all_combo_list_current_genes = itertools.product(list_of_species_1_genes_in_group,list_of_species_2_genes_in_group)
    all_combo_list_current_genes = list(map(list,all_combo_list_current_genes))
    current_list_of_pairs = pd.DataFrame(all_combo_list_current_genes,columns = [common_name_1,common_name_2])
    current_list_of_pairs['Group Number'] = group_number
    all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)


all_pairs_to_evaluate_for_functional_conservation['Species 1 Score'] = np.nan
all_pairs_to_evaluate_for_functional_conservation['Species 2 Score'] = np.nan

/tmp/ipykernel_2026627/195673793.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/195673793.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/195673793.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_pairs_to_evaluate_for_functional_conservation = all_pairs_to_evaluate_for_functional_conservation.append(current_list_of_pairs)
/tmp/ipykernel_2026627/195673793.py:10: FutureWarning: The frame.append method 

In [8]:
trimmed_species_1_cococonet = coconet_species_one[coconet_species_one.columns.intersection(cross_species_n_m_genes[common_name_1].to_list())]
trimmed_species_1_cococonet = trimmed_species_1_cococonet[trimmed_species_1_cococonet.index.isin(cross_species_n_m_genes[common_name_1].to_list())]
double_species_1_trimmed_cococonet = trimmed_species_1_cococonet[trimmed_species_1_cococonet.columns.intersection(cross_species_map_one_to_one[common_name_1].to_list())]
double_species_1_trimmed_cococonet = double_species_1_trimmed_cococonet.replace(1,0)

trimmed_species_2_cococonet = coconet_species_two[coconet_species_two.columns.intersection(cross_species_n_m_genes[common_name_2].to_list())]
trimmed_species_2_cococonet = trimmed_species_2_cococonet[trimmed_species_2_cococonet.index.isin(cross_species_n_m_genes[common_name_2].to_list())]
double_species_2_trimmed_cococonet = trimmed_species_2_cococonet[trimmed_species_2_cococonet.columns.intersection(cross_species_map_one_to_one[common_name_2].to_list())]
double_species_2_trimmed_cococonet = double_species_2_trimmed_cococonet.replace(1,0)

In [11]:

species_1_cococonet_ranked = trimmed_species_1_cococonet.rank()
species_2_cococonet_ranked = trimmed_species_2_cococonet.rank()

In [12]:
top_10_species_1_genes = np.array(
    [double_species_1_trimmed_cococonet.T[c].nlargest(10).index.values for c in double_species_1_trimmed_cococonet.T]
)  # using pair list above, cut down top 10 list to relevant genes, probably by adding list as a column in panda and then filtering panda to index of pair list
top_10_species_1_genes_dataframe = pd.DataFrame(
    data=top_10_species_1_genes,
    index=double_species_1_trimmed_cococonet.index,
    columns=[
        "One",
        "Two",
        "Three",
        "Four",
        "Five",
        "Six",
        "Seven",
        "Eight",
        "Nine",
        "Ten",
    ],
)
top_10_species_1_genes_dataframe

One           Two         Three          Four  \
LOC103438296  LOC103418749  LOC103448113  LOC103408142  LOC103429549   
LOC103409995  LOC103455036  LOC103410725  LOC103454690  LOC103400650   
LOC103441767  LOC103454690  LOC103453665  LOC103441811  LOC103439644   
LOC103410973  LOC103401039  LOC103425288  LOC103447218  LOC103403608   
LOC103423413  LOC103436534  LOC103446382  LOC103427257  LOC103402989   
...                    ...           ...           ...           ...   
LOC103419335  LOC103420171  LOC103437782  LOC103403556  LOC103428011   
LOC103439183  LOC103431652  LOC103424141  LOC103451022  LOC103435432   
LOC103405742  LOC103445640  LOC103412347  LOC103402210  LOC103439133   
LOC103425628  LOC103451787  LOC103440264  LOC103446382  LOC103433613   
LOC103449869  LOC103440997  LOC103438582  LOC103442391  LOC103402662   

                      Five           Six         Seven         Eight  \
LOC103438296  LOC103436881  LOC103453422  LOC103426390  LOC103418400   
LOC103409995  LOC103439133  LOC103408015  LOC103402376  LOC103448355   
LOC103441767  LOC103449667  LOC103443036  LOC103455036  LOC103420171   
LOC103410973  LOC103417271  LOC103411750  LOC103424151  LOC103412177   
LOC103423413  LOC103412560  LOC103400845  LOC103412422  LOC103453657   
...                    ...           ...           ...           ...   
LOC103419335  LOC103422773  LOC103438476  LOC103447971  LOC103453114   
LOC103439183  LOC103409271  LOC103401877  LOC103418400  LOC103446388   
LOC103405742  LOC103402864  LOC103449662  LOC103436506  LOC103449667   
LOC103425628  LOC103405578  LOC103421499  LOC103440437  LOC103432600   
LOC103449869  LOC103435455  LOC103422975  LOC103431652  LOC103415687   

                      Nine           Ten  
LOC103438296  LOC103438314  LOC103409057  
LOC103409995  LOC103455033  LOC103453422  
LOC103441767  LOC103429152  LOC103445151  
LOC103410973  LOC103440449  LOC103443710  
LOC103423413  LOC103434156  LOC103401314  
...                    ...           ...  
LOC103419335  LOC103439140  LOC103447157  
LOC103439183  LOC103449492  LOC103402662  
LOC103405742  LOC103401288  LOC103456272  
LOC103425628  LOC108169259  LOC103455892  
LOC103449869  LOC103432750  LOC103409057  

[12500 rows x 10 columns]

In [13]:
top_10_species_1_genes_as_species_2 = top_10_species_1_genes_dataframe.replace(to_replace=dictionary_mapper_one_to_two)
top_10_species_1_genes_as_species_2

One         Two       Three        Four        Five  \
LOC103438296  LOC8070533  LOC8054304  LOC8085969  LOC8063006  LOC8068174   
LOC103409995  LOC8070615  LOC8074512  LOC8073097  LOC8069538  LOC8077997   
LOC103441767  LOC8073097  LOC8075479  LOC8054471  LOC8065870  LOC8055085   
LOC103410973  LOC8064784  LOC8055047  LOC8071761  LOC8059729  LOC8080569   
LOC103423413  LOC8064300  LOC8077476  LOC8057401  LOC8057195  LOC8071186   
...                  ...         ...         ...         ...         ...   
LOC103419335  LOC8081400  LOC8058353  LOC8071187  LOC8066413  LOC8083658   
LOC103439183  LOC8075692  LOC8078593  LOC8077463  LOC8056115  LOC8065170   
LOC103405742  LOC8054341  LOC8077200  LOC8064274  LOC8077997  LOC8079372   
LOC103425628  LOC8078996  LOC8054345  LOC8077476  LOC8085430  LOC8071032   
LOC103449869  LOC8071322  LOC8083670  LOC8066279  LOC8063092  LOC8059094   

                     Six       Seven       Eight        Nine         Ten  
LOC103438296  LOC8067771  LOC8073352  LOC8069056  LOC8065822  LOC8074504  
LOC103409995  LOC8083969  LOC8062815  LOC8072704  LOC8065090  LOC8067771  
LOC103441767  LOC8085400  LOC8070615  LOC8081400  LOC8066824  LOC8075881  
LOC103410973  LOC8070014  LOC8075715  LOC8060512  LOC8062485  LOC8075013  
LOC103423413  LOC8060669  LOC8073287  LOC8059277  LOC8066521  LOC8085912  
...                  ...         ...         ...         ...         ...  
LOC103419335  LOC8063925  LOC8075267  LOC8073279  LOC8055342  LOC8071634  
LOC103439183  LOC8063499  LOC8069056  LOC8080059  LOC8057815  LOC8063092  
LOC103405742  LOC8063055  LOC8063708  LOC8055085  LOC8070298  LOC8056480  
LOC103425628  LOC8057473  LOC8077149  LOC8076003  LOC8073567  LOC8081878  
LOC103449869  LOC8061616  LOC8075692  LOC8067972  LOC8064383  LOC8074504  

[12500 rows x 10 columns]

In [15]:
all_pairs_to_evaluate_for_functional_conservation

apple     sorghum Group Number  Species 1 Score  Species 2 Score
0   LOC103444819  LOC8081914            0              NaN              NaN
1   LOC103444819  LOC8155288            0              NaN              NaN
0   LOC103401548  LOC8054161            1              NaN              NaN
0   LOC103417271  LOC8080569            2              NaN              NaN
0   LOC103426806  LOC8083888            3              NaN              NaN
..           ...         ...          ...              ...              ...
3   LOC103425265  LOC8155665         7110              NaN              NaN
4   LOC103401664  LOC8155665         7110              NaN              NaN
5   LOC108169413  LOC8155665         7110              NaN              NaN
6   LOC103424311  LOC8155665         7110              NaN              NaN
7   LOC103407206  LOC8155665         7110              NaN              NaN

[44580 rows x 5 columns]

In [16]:
have_species_1_pairs = all_pairs_to_evaluate_for_functional_conservation.loc[all_pairs_to_evaluate_for_functional_conservation[common_name_1].isin(top_10_species_1_genes_as_species_2.index)]
trimmed_all_gene_pairs_for_fc = have_species_1_pairs.loc[have_species_1_pairs[common_name_2].isin(trimmed_species_2_cococonet.index)]
trimmed_all_gene_pairs_for_fc = trimmed_all_gene_pairs_for_fc.reset_index(drop = True)
trimmed_all_gene_pairs_for_fc

apple     sorghum Group Number  Species 1 Score  Species 2 Score
0      LOC103444819  LOC8081914            0              NaN              NaN
1      LOC103444819  LOC8155288            0              NaN              NaN
2      LOC103401548  LOC8054161            1              NaN              NaN
3      LOC103417271  LOC8080569            2              NaN              NaN
4      LOC103426806  LOC8083888            3              NaN              NaN
...             ...         ...          ...              ...              ...
19494  LOC103450923  LOC8077323         7107              NaN              NaN
19495  LOC103455790  LOC8077323         7107              NaN              NaN
19496  LOC103440894  LOC8077323         7107              NaN              NaN
19497  LOC103432817  LOC8072511         7109              NaN              NaN
19498  LOC103437184  LOC8072511         7109              NaN              NaN

[19499 rows x 5 columns]

In [18]:
for two_genes in trimmed_all_gene_pairs_for_fc.iterrows():
    current_species_1_gene = two_genes[1][common_name_1]
    current_species_2_gene = two_genes[1][common_name_2]
    finger_print_genes = top_10_species_1_genes_as_species_2.loc[current_species_1_gene].to_list()
    gene_ranks_in_species_2 = species_2_cococonet_ranked.loc[species_2_cococonet_ranked.index.isin(finger_print_genes), current_species_2_gene]
    avg_rank_in_species_2 = gene_ranks_in_species_2.mean()
    index_from_pairs = two_genes[0]
    trimmed_all_gene_pairs_for_fc.at[index_from_pairs, 'Species 1 Score'] = avg_rank_in_species_2

In [20]:
top_10_species_2_genes = np.array(
    [double_species_2_trimmed_cococonet.T[c].nlargest(10).index.values for c in double_species_2_trimmed_cococonet.T]
)  # using pair list above, cut down top 10 list to relevant genes, probably by adding list as a column in panda and then filtering panda to index of pair list
top_10_species_2_genes_dataframe = pd.DataFrame(
    data=top_10_species_2_genes,
    index=double_species_2_trimmed_cococonet.index,
    columns=[
        "One",
        "Two",
        "Three",
        "Four",
        "Five",
        "Six",
        "Seven",
        "Eight",
        "Nine",
        "Ten",
    ],
)
top_10_species_2_genes_dataframe

One         Two       Three        Four        Five  \
LOC8059226  LOC8085267  LOC8082416  LOC8057906  LOC8062421  LOC8084951   
LOC8059227  LOC8058644  LOC8072025  LOC8078135  LOC8078160  LOC8057871   
LOC8061368  LOC8064301  LOC8072006  LOC8082736  LOC8057060  LOC8065677   
LOC8059230  LOC8060324  LOC8063395  LOC8085267  LOC8085969  LOC8062485   
LOC8059233  LOC8064740  LOC8086276  LOC8054327  LOC8069311  LOC8066948   
...                ...         ...         ...         ...         ...   
LOC8069246  LOC8057815  LOC8086252  LOC8060494  LOC8084519  LOC8060429   
LOC8069247  LOC8055974  LOC8060565  LOC8060410  LOC8062043  LOC8057815   
LOC8069249  LOC8059819  LOC8072329  LOC8065168  LOC8073187  LOC8155678   
LOC8066401  LOC8054193  LOC8062421  LOC8075692  LOC8063339  LOC8086274   
LOC8069251  LOC8079574  LOC8077553  LOC8058530  LOC8082416  LOC8057351   

                   Six       Seven       Eight        Nine         Ten  
LOC8059226  LOC8086274  LOC8077463  LOC8054193  LOC8055047  LOC8079574  
LOC8059227  LOC8072006  LOC8065183  LOC8081760  LOC8086174  LOC8085082  
LOC8061368  LOC8061365  LOC8078135  LOC8077716  LOC8082831  LOC8066480  
LOC8059230  LOC8054345  LOC8074743  LOC8076406  LOC8084666  LOC8084676  
LOC8059233  LOC8060278  LOC8062869  LOC8084676  LOC8083947  LOC8069289  
...                ...         ...         ...         ...         ...  
LOC8069246  LOC8056158  LOC8078086  LOC8074713  LOC8062485  LOC8062907  
LOC8069247  LOC8065093  LOC8078015  LOC8061158  LOC8082202  LOC8078086  
LOC8069249  LOC8082318  LOC8079639  LOC8063471  LOC8068028  LOC8058406  
LOC8066401  LOC8065267  LOC8070472  LOC8059520  LOC8086253  LOC8056137  
LOC8069251  LOC8064304  LOC8063339  LOC8058997  LOC8072897  LOC8055047  

[9164 rows x 10 columns]

In [21]:
top_10_species_2_genes_as_species_1 = top_10_species_2_genes_dataframe.replace(to_replace=dictionary_mapper_dos_to_uno)
top_10_species_2_genes_as_species_1

One           Two         Three          Four  \
LOC8059226  LOC103453780  LOC103446543  LOC103400677  LOC103413123   
LOC8059227  LOC103452376  LOC103437570  LOC103444480  LOC103405985   
LOC8061368  LOC103423476  LOC103439790  LOC108172383  LOC103445340   
LOC8059230  LOC103436461  LOC103449813  LOC103453780  LOC103408142   
LOC8059233  LOC103443482  LOC103428159  LOC103439470  LOC103403848   
...                  ...           ...           ...           ...   
LOC8069246  LOC103449492  LOC103425348  LOC103453310  LOC103445344   
LOC8069247  LOC103448618  LOC103405973  LOC103418084  LOC103439624   
LOC8069249  LOC103410224  LOC103446078  LOC103413834  LOC103403996   
LOC8066401  LOC103439149  LOC103413123  LOC103431652  LOC103440214   
LOC8069251  LOC103436071  LOC103447977  LOC103424668  LOC103446543   

                    Five           Six         Seven         Eight  \
LOC8059226  LOC103447685  LOC103436771  LOC103451022  LOC103439149   
LOC8059227  LOC103456354  LOC103439790  LOC103410335  LOC103430301   
LOC8061368  LOC103446395  LOC103402612  LOC103444480  LOC103405062   
LOC8059230  LOC103440449  LOC103440264  LOC103429309  LOC103401129   
LOC8059233  LOC103450732  LOC103425882  LOC103436908  LOC103449751   
...                  ...           ...           ...           ...   
LOC8069246  LOC103423867  LOC103405343  LOC103441759  LOC103454475   
LOC8069247  LOC103449492  LOC103427783  LOC103432065  LOC103454726   
LOC8069249  LOC103400610  LOC103403719  LOC103405970  LOC103422579   
LOC8066401  LOC103436771  LOC103403471  LOC103438686  LOC103401906   
LOC8069251  LOC103412304  LOC103400276  LOC103440214  LOC103428347   

                    Nine           Ten  
LOC8059226  LOC103425288  LOC103436071  
LOC8059227  LOC103425358  LOC103449010  
LOC8061368  LOC103447999  LOC103439617  
LOC8059230  LOC103451940  LOC103449751  
LOC8059233  LOC103440510  LOC103454580  
...                  ...           ...  
LOC8069246  LOC103440449  LOC103449936  
LOC8069247  LOC103453178  LOC103441759  
LOC8069249  LOC103410578  LOC103436064  
LOC8066401  LOC103414841  LOC103437637  
LOC8069251  LOC103432563  LOC103425288  

[9164 rows x 10 columns]

In [22]:
for two_genes in trimmed_all_gene_pairs_for_fc.iterrows():
    current_species_1_gene = two_genes[1][common_name_1]
    current_species_2_gene = two_genes[1][common_name_2]
    finger_print_genes = top_10_species_2_genes_as_species_1.loc[current_species_2_gene].to_list()
    gene_ranks_in_species_1 = species_1_cococonet_ranked.loc[species_1_cococonet_ranked.index.isin(finger_print_genes), current_species_1_gene]
    avg_rank_in_species_1 = gene_ranks_in_species_1.mean()
    index_from_pairs = two_genes[0]
    trimmed_all_gene_pairs_for_fc.loc[index_from_pairs, 'Species 2 Score'] = avg_rank_in_species_1

In [23]:
trimmed_all_gene_pairs_for_fc

apple     sorghum Group Number  Species 1 Score  Species 2 Score
0      LOC103444819  LOC8081914            0      7172.300000      9381.555556
1      LOC103444819  LOC8155288            0      7508.100000     11504.400000
2      LOC103401548  LOC8054161            1      7666.400000     10479.888889
3      LOC103417271  LOC8080569            2      7854.300000      9002.700000
4      LOC103426806  LOC8083888            3      7853.100000     11470.000000
...             ...         ...          ...              ...              ...
19494  LOC103450923  LOC8077323         7107      3705.666667      6286.333333
19495  LOC103455790  LOC8077323         7107      5110.100000      8675.333333
19496  LOC103440894  LOC8077323         7107      5344.200000      8660.222222
19497  LOC103432817  LOC8072511         7109      7042.100000      9200.200000
19498  LOC103437184  LOC8072511         7109      6783.100000     10885.700000

[19499 rows x 5 columns]

In [25]:
Number_of_species_1_genes = len(top_10_species_1_genes_as_species_2)
Number_of_species_2_genes = len(top_10_species_2_genes_as_species_1)


species_1_score_divisor = Number_of_species_2_genes - 4.5
species_2_score_divisor = Number_of_species_1_genes-4.5

9159.5
9159.5


In [26]:
trimmed_all_gene_pairs_for_fc['Species 1 Score'] = trimmed_all_gene_pairs_for_fc['Species 1 Score']/species_1_score_divisor
trimmed_all_gene_pairs_for_fc['Species 2 Score'] = trimmed_all_gene_pairs_for_fc['Species 2 Score']/species_2_score_divisor
trimmed_all_gene_pairs_for_fc['Total Score'] = trimmed_all_gene_pairs_for_fc[['Species 1 Score','Species 2 Score']].mean(axis = 1)
trimmed_all_gene_pairs_for_fc

apple     sorghum Group Number  Species 1 Score  \
0      LOC103444819  LOC8081914            0         0.783045   
1      LOC103444819  LOC8155288            0         0.819706   
2      LOC103401548  LOC8054161            1         0.836989   
3      LOC103417271  LOC8080569            2         0.857503   
4      LOC103426806  LOC8083888            3         0.857372   
...             ...         ...          ...              ...   
19494  LOC103450923  LOC8077323         7107         0.404571   
19495  LOC103455790  LOC8077323         7107         0.557902   
19496  LOC103440894  LOC8077323         7107         0.583460   
19497  LOC103432817  LOC8072511         7109         0.768830   
19498  LOC103437184  LOC8072511         7109         0.740554   

       Species 2 Score  Total Score  
0             0.750795     0.766920  
1             0.920683     0.870195  
2             0.838693     0.837841  
3             0.720475     0.788989  
4             0.917930     0.887651  
...                ...          ...  
19494         0.503088     0.453829  
19495         0.694277     0.626089  
19496         0.693067     0.638264  
19497         0.736281     0.752556  
19498         0.871170     0.805862  

[19499 rows x 6 columns]